In [1]:
import numpy as np
from cogent3 import get_app, open_data_store
import plotly.express as px
from clock_project.genome_analysis.homolog_analysis import (gather_fasta_paths2, pairwise_jsd_matrix, prepare_dataframes,  
                                                            common_name_renamer, filter, jsd_genetic_distance_scatters)
import json
import os
import numpy as np
import glob
from cogent3 import get_app, open_data_store


In [2]:
base_dir = "/Users/gulugulu/Desktop/honours/data_local/whole_genome_mammal87/sampled_homologies_3000"

homology_fa_paths2 = gather_fasta_paths2(base_dir)

In [3]:
len(homology_fa_paths2)

3963

In [42]:
loader = get_app("load_unaligned", format="fasta", moltype="dna")
codon_aligner = get_app("progressive_align", "codon", unique_guides=True)
cpos3 = get_app("take_codon_positions", 3)

In [43]:
valid_homology_list_4000 = []
prob_homology_list_4000 = []
species_less_than_3_4000 = []
small_sample_size_4000 = []
short_alignment_4000 = []
alignment_length_4000 = {}

alignment_prob_homology_count = 0
distance_prob_homology_count = 0
all_filtered_path_count = 0

In [40]:
aln_output_dir = '/Users/gulugulu/repos/PuningAnalysis/data/ensembl_ortholog_sequences/homologies_alignment_common_name_350_threshold'
seq_output_dir = '/Users/gulugulu/repos/PuningAnalysis/data/ensembl_ortholog_sequences/homologies_sequence_common_name_350_threshold'

In [47]:
path_info.keys()

dict_keys(['ENSG00000157184.fa', 'ENSG00000116679.fa', 'ENSG00000143368.fa', 'ENSG00000197136.fa', 'ENSG00000248746.fa', 'ENSG00000159164.fa', 'ENSG00000120457.fa', 'ENSG00000198797.fa', 'ENSG00000197658.fa', 'ENSG00000127124.fa', 'ENSG00000023839.fa', 'ENSG00000174684.fa', 'ENSG00000117707.fa', 'ENSG00000185278.fa', 'ENSG00000197147.fa', 'ENSG00000197106.fa', 'ENSG00000165494.fa', 'ENSG00000138161.fa', 'ENSG00000110344.fa', 'ENSG00000133019.fa', 'ENSG00000265203.fa', 'ENSG00000198730.fa', 'ENSG00000204478.fa', 'ENSG00000255855.fa', 'ENSG00000116194.fa', 'ENSG00000203857.fa', 'ENSG00000173898.fa', 'ENSG00000171488.fa', 'ENSG00000143278.fa', 'ENSG00000198198.fa', 'ENSG00000126705.fa', 'ENSG00000176986.fa', 'ENSG00000187151.fa', 'ENSG00000162775.fa', 'ENSG00000073756.fa', 'ENSG00000254685.fa', 'ENSG00000123836.fa', 'ENSG00000154143.fa', 'ENSG00000166507.fa', 'ENSG00000170382.fa', 'ENSG00000236287.fa', 'ENSG00000119285.fa', 'ENSG00000166189.fa', 'ENSG00000151079.fa', 'ENSG00000162654.fa',

In [48]:


# Assume homology_fa_paths is defined somewhere
for name in path_info.keys():
    path = os.path.join(base_dir, name)
    print(path)
    file_name = os.path.basename(path.rstrip('/'))
    seqs = loader(path)
    seqs_filtered = filter(seqs)  # Ensure filter is correctly defined and imported
    try:
        seqs_filtered_no_stop_codon = seqs_filtered.trim_stop_codons(strict=True)
        if seqs_filtered_no_stop_codon.num_seqs < 3:
            species_less_than_3_4000.append(path)
        else:
            aligned = codon_aligner(seqs_filtered_no_stop_codon)
            just3rd_aligned = cpos3(aligned)
            just3rd_aligned_no_degenerates = just3rd_aligned.no_degenerates(motif_length=3)
            alignment_length = just3rd_aligned_no_degenerates.get_lengths()[0]
            print(alignment_length)
            alignment_length_4000[file_name] = alignment_length
            
            if just3rd_aligned_no_degenerates.num_seqs < 30:
                small_sample_size_4000.append(path)
                print(f"Path added to small size: {path} with length {just3rd_aligned_no_degenerates.num_seqs}")
            
            else:  
                valid_homology_list_4000.append(path)
                print(f"Path added to valid_homology_list: {path} with length {alignment_length}, sample size {just3rd_aligned_no_degenerates.num_seqs}")
                file_name_path = os.path.basename(path).rsplit('.', 1)[0] + ".json"
                print(file_name)
                renamed_alignment = common_name_renamer(just3rd_aligned_no_degenerates)
                renamed_seqs = common_name_renamer(seqs_filtered_no_stop_codon)
                output_path_alignment = os.path.join(aln_output_dir, file_name_path)
                output_path_sequence = os.path.join(seq_output_dir, file_name_path)
                with open (output_path_alignment, 'w') as outfile1:
                    json.dump(renamed_alignment.to_json(), outfile1)
        # print(f"Alignment saved to {output_path_alignment}")

                with open (output_path_sequence, 'w') as outfile2:
                    json.dump(renamed_seqs.to_json(), outfile2)
            # else:
            #     pairwise_distance = just3rd_aligned_no_degenerates.distance_matrix(calc='tn93', show_progress=False, drop_invalid=True)
            #     pairwise_distance_array = pairwise_distance.array
                
            #     if len(np.unique(pairwise_distance_array)) < 190:
            #         small_sample_size.append(path)
            #     else:
                


    except Exception as e:
        print(e)
        prob_homology_list_4000.append(path)
        if 'distance_matrix' in str(e):
            alignment_prob_homology_count += 1
        elif 'array' in str(e):
            distance_prob_homology_count += 1
        elif 'num_seqs' in str(e):
            print("Error related to 'num_seqs'")


/Users/gulugulu/Desktop/honours/data_local/whole_genome_mammal87/sampled_homologies_3000/ENSG00000157184.fa
423
Path added to valid_homology_list: /Users/gulugulu/Desktop/honours/data_local/whole_genome_mammal87/sampled_homologies_3000/ENSG00000157184.fa with length 423, sample size 60
ENSG00000157184.fa
/Users/gulugulu/Desktop/honours/data_local/whole_genome_mammal87/sampled_homologies_3000/ENSG00000116679.fa
390
Path added to valid_homology_list: /Users/gulugulu/Desktop/honours/data_local/whole_genome_mammal87/sampled_homologies_3000/ENSG00000116679.fa with length 390, sample size 59
ENSG00000116679.fa
/Users/gulugulu/Desktop/honours/data_local/whole_genome_mammal87/sampled_homologies_3000/ENSG00000143368.fa
363
Path added to valid_homology_list: /Users/gulugulu/Desktop/honours/data_local/whole_genome_mammal87/sampled_homologies_3000/ENSG00000143368.fa with length 363, sample size 55
ENSG00000143368.fa
/Users/gulugulu/Desktop/honours/data_local/whole_genome_mammal87/sampled_homologie

In [29]:
np.mean(list(alignment_length_4000.values()))

141.6220115416323

In [ ]:
import json

# Output directory for the PDFs
aln_output_dir = '/Users/gulugulu/repos/PuningAnalysis/data/ensembl_ortholog_sequences/homologies_alignments_common_name_2' 
seq_output_dir = '/Users/gulugulu/repos/PuningAnalysis/data/ensembl_ortholog_sequences/homologies_sequence_common_name_2'
aln_lengths = []
for path in valid_homology_list_4000:
    try: 
        aln, seq = get_just3rd_aligned_no_degenerates(path)
        print(aln.get_lengths()[0])
        aln_lengths.append(aln.get_lengths()[0])
        file_name = os.path.basename(path).rsplit('.', 1)[0] + ".json"
        renamed_alignment = common_name_renamer(aln)
        renamed_seqs = common_name_renamer(seq)
        output_path_alignment = os.path.join(aln_output_dir, file_name)
        output_path_sequence = os.path.join(seq_output_dir, file_name)

        with open (output_path_alignment, 'w') as outfile1:
            json.dump(renamed_alignment.to_json(), outfile1)
        # print(f"Alignment saved to {output_path_alignment}")

        with open (output_path_sequence, 'w') as outfile2:
            json.dump(renamed_seqs.to_json(), outfile2)
        # print(f"Sequence saved to {output_path_sequence}")
    except Exception as e:
        print(Exception)

In [5]:
# valid_homology_list2 = []
# prob_homology_list2 = []
# species_less_than_3 = []
# small_sample_size2 = []
# short_alignment2 = []
# alignment_length = {}

# alignment_prob_homology_count = 0
# distance_prob_homology_count = 0
# all_filtered_path_count = 0

# # Assume homology_fa_paths is defined somewhere
# for path in homology_fa_paths1:
#     file_name = os.path.basename(path.rstrip('/'))
#     seqs = loader(path)
#     seqs_filtered = filter(seqs)  # Ensure filter is correctly defined and imported
#     try:
#         seqs_filtered_no_stop_codon = seqs_filtered.trim_stop_codons(strict=True)
#         if seqs_filtered_no_stop_codon.num_seqs < 3:
#             species_less_than_3.append(path)
#         else:
#             aligned = codon_aligner(seqs_filtered_no_stop_codon)
#             just3rd_aligned = cpos3(aligned)
#             just3rd_aligned_no_degenerates = just3rd_aligned.no_degenerates(motif_length=3)
#             alignment_length = just3rd_aligned_no_degenerates.get_lengths()[0]
#             print(alignment_length)
            
#             if alignment_length < 200:
#                 short_alignment2.append(path)
#                 print(f"Path added to short_alignment: {path} with length {alignment_length}")
            
#             elif just3rd_aligned_no_degenerates.num_seqs < 10:
#                 small_sample_size2.append(path)
#                 print(f"Path added to small size: {path} with length {just3rd_aligned_no_degenerates.num_seqs}")
            
#             else:  
#                     valid_homology_list2.append(path)
#                     print(f"Path added to valid_homology_list: {path} with length {alignment_length}, sample size {just3rd_aligned_no_degenerates.num_seqs}")

#             # else:
#             #     pairwise_distance = just3rd_aligned_no_degenerates.distance_matrix(calc='tn93', show_progress=False, drop_invalid=True)
#             #     pairwise_distance_array = pairwise_distance.array
                
#             #     if len(np.unique(pairwise_distance_array)) < 190:
#             #         small_sample_size.append(path)
#             #     else:
                


#     except Exception as e:
#         prob_homology_list2.append(path)
#         if 'distance_matrix' in str(e):
#             alignment_prob_homology_count += 1
#         elif 'array' in str(e):
#             distance_prob_homology_count += 1
#         elif 'num_seqs' in str(e):
#             print("Error related to 'num_seqs'")


In [41]:
len(valid_homology_list_4000), len(prob_homology_list_4000), len(short_alignment_4000), len(species_less_than_3_4000), len(small_sample_size_4000)

(103, 1444, 2321, 96, 9)

In [15]:
with open ('valid_path_new.json', 'w') as outfile:
    json.dump(valid_homology_list_4000, outfile)

In [18]:
px.histogram(alignment_length_4000.values())

In [36]:
path_info = {}
for gene, length in alignment_length_4000.items():
    if length > 350:
        path_info[gene] = length


In [49]:
len(path_info)

157

In [37]:
np.mean(list(path_info.values()))

518.3885350318471

In [38]:
len(path_info.keys())

157

In [6]:
# def get_pairwise_jsd_genetic_distance(path):
#     seqs = loader(path)
#     seqs_filtered = filter(seqs)
#     seqs_filtered_no_stop_codon = seqs_filtered.trim_stop_codons(strict=True)
#     aligned = codon_aligner(seqs_filtered_no_stop_codon)
#     just3rd_aligned = cpos3(aligned)
#     just3rd_aligned_no_degenerates = just3rd_aligned.no_degenerates(motif_length=3)
#     alignment_length = just3rd_aligned_no_degenerates.seq_len
#     taxa_num = just3rd_aligned_no_degenerates.num_seqs
#     pairwise_distance = just3rd_aligned_no_degenerates.distance_matrix(calc='tn93', show_progress=False, drop_invalid=True)
#     pairwise_distance_array = pairwise_distance.array
#     nuc_freqs = just3rd_aligned_no_degenerates.probs_per_seq()
#     sub_nuc_freqs = {}
#     for key in pairwise_distance.keys():
#         sub_nuc_freqs[key] = nuc_freqs[key]

#     pairwise_jsd = pairwise_jsd_matrix(sub_nuc_freqs)
#     pairwise_distance_values = pairwise_distance_array[np.triu_indices(n=pairwise_distance_array.shape[0], k=1)]
#     pairwise_jsd_values = pairwise_jsd[np.triu_indices(n=pairwise_jsd.shape[0], k=1)]
#     num_compare = pairwise_jsd.shape[0]
#     num_compare2 = len(pairwise_jsd_values)

#     return pairwise_distance_values, pairwise_jsd_values, alignment_length, taxa_num, num_compare, num_compare2

In [7]:
# import os
# from scipy.stats import pearsonr

# species_data = {}
# correlation_info = {}
# for path in valid_homology_list_4000:
#     filename = os.path.basename(path)
#     gene_name = os.path.splitext(filename)[0]
#     pairwise_distance, pairwise_jsd, alignment_length, taxa_num, num_compare, num_compare2 = get_pairwise_jsd_genetic_distance(path)
#     col, p_value = pearsonr(pairwise_jsd, pairwise_distance)
#     correlation_info[gene_name] = {'correlation_factor': col, 'p_value': p_value}
#     species_data[gene_name]  = {'pairwise_distance': pairwise_distance, 'pairwise_jsd': pairwise_jsd, 'col': col, 'p_value': p_value, 'alignment_length': alignment_length, 'taxa number': taxa_num, 'number of taxa2': num_compare, 'number of comparison': num_compare2}


# for key, value in species_data.items():
#     for subkey, subvalue in value.items():
#         if isinstance(subvalue, np.ndarray):
#             species_data[key][subkey] = subvalue.tolist()

# with open ('/Users/gulugulu/repos/PuningAnalysis/results/output_data/species_data2.json', 'w') as outfile2:
#     json.dump(species_data, outfile2)



In [6]:
def get_just3rd_aligned_no_degenerates(path):
    """Processes a sequence file to align and filter third codon positions without degenerates."""
    seqs = loader(path)
    seqs_filtered = filter(seqs)
    seqs_filtered_no_stop_codon = seqs_filtered.trim_stop_codons(strict=True)
    aligned = codon_aligner(seqs_filtered_no_stop_codon)
    just3rd_aligned = cpos3(aligned)
    just3rd_aligned_no_degenerates = just3rd_aligned.no_degenerates(motif_length=3)
    return just3rd_aligned_no_degenerates, seqs_filtered


In [118]:
# with open ('/Users/gulugulu/repos/PuningAnalysis/results/output_data/valid_path.json', 'w') as outfile:
#     json.dump(valid_homology_list, outfile)

In [4]:
import json

# Output directory for the PDFs
aln_output_dir = '/Users/gulugulu/repos/PuningAnalysis/data/ensembl_ortholog_sequences/homologies_alignments_common_name_2' 
seq_output_dir = '/Users/gulugulu/repos/PuningAnalysis/data/ensembl_ortholog_sequences/homologies_sequence_common_name_2'
aln_lengths = []
for path in valid_homology_list_4000:
    try: 
        aln, seq = get_just3rd_aligned_no_degenerates(path)
        print(aln.get_lengths()[0])
        aln_lengths.append(aln.get_lengths()[0])
        file_name = os.path.basename(path).rsplit('.', 1)[0] + ".json"
        renamed_alignment = common_name_renamer(aln)
        renamed_seqs = common_name_renamer(seq)
        output_path_alignment = os.path.join(aln_output_dir, file_name)
        output_path_sequence = os.path.join(seq_output_dir, file_name)

        with open (output_path_alignment, 'w') as outfile1:
            json.dump(renamed_alignment.to_json(), outfile1)
        # print(f"Alignment saved to {output_path_alignment}")

        with open (output_path_sequence, 'w') as outfile2:
            json.dump(renamed_seqs.to_json(), outfile2)
        # print(f"Sequence saved to {output_path_sequence}")
    except Exception as e:
        print(Exception)
        


UnsupportedOperation: not readable

In [110]:
path = '/Users/gulugulu/Desktop/honours/data_local/whole_genome_mammal87/sampled_homologies/ENSG00000116221.fa'
pairwise_distance, pairwise_jsd, alignment_length, taxa_num, num_compare, num_compare2 = get_pairwise_jsd_genetic_distance(path)
import plotly.graph_objects as go

# Create the scatter plot
fig = go.Figure(data=go.Scatter(x=np.log10(pairwise_jsd), y=pairwise_distance, mode='markers'))

# Update plot layout
fig.update_layout(
    title='Gene: MRPL37',
    xaxis_title='Log10(Jensen-Shannon Divergence)',
    yaxis_title='Pairwise Distance (tn93)',
    template="plotly_white"  
)

# Show the plot
fig.show()
fig.write_image('jsd_genetic_distance_scatters_MRPL37.pdf')

In [2]:
with open ('/Users/gulugulu/repos/PuningAnalysis/results/output_data/species_data.json','r') as species_data_file:
    species_data = json.load(species_data_file)
species_df = prepare_dataframes(species_data)
jsd_distance_sub_fig = jsd_genetic_distance_scatters(species_df)
jsd_distance_sub_fig.write_image('jsd_genetic_distance_scatters.pdf')

In [ ]:
# cfs = {name: species_data[name]['col'] for name in species_data.keys()}
# pvs = {name: species_data[name]['p_value'] for name in species_data.keys()}
# for gene in species_data.keys():
#     dis_col = correlation(species_data[gene]['pairwise_distance'], species_data[gene]['pairwise_jsd'])
#     species_data[gene]['distance correlation'] = dis_col
# dcs = [species_data[gene]['distance correlation'] for gene in species_data.keys()]

In [ ]:
# import pandas as pd

# def summarize_stat(data):
#     df = pd.DataFrame(list(data.items()), columns=['Gene', 'Value'])
#     summary_stats = {
#         'Mean': df['Value'].mean(),
#         'Median': df['Value'].median(),
#         'Standard Deviation': df['Value'].std(),
#         'Variance': df['Value'].var(),
#         'Minimum': df['Value'].min(),
#         'Maximum': df['Value'].max(),
#         'Range': df['Value'].max() - df['Value'].min()
#     }
#     summary_df = pd.DataFrame(summary_stats, index=[0])

#     return summary_df

In [ ]:
# # New directory path
# new_path_prefix = '/Users/gulugulu/Desktop/honours/data_local/whole_genome_mammal87/valid_homologies/'

# # Generate the valid_path list
# valid_path_model_fitting = [new_path_prefix + file.split('/')[-1].replace('.json', '.fa') for file in lf_json_files]

# with open ('../../results/output_data/valid_path_model_fitting', 'w') as outfile:
#     json.dump(valid_path_model_fitting, outfile)

In [14]:
import os
import glob
import plotly.io as pio
from cogent3 import get_app

# Directory and pattern to find JSON files
dir = '/Users/gulugulu/repos/PuningAnalysis/results/output_data/model_fitting_result'
pattern = os.path.join(dir, '*.json')

# Use glob.glob to find all files matching the pattern
lf_json_files = glob.glob(pattern)

# Output directory for the PDFs
pdf_output_dir = '/Users/gulugulu/repos/PuningAnalysis/results/figures/model_fitting_result_figures_GN'
os.makedirs(pdf_output_dir, exist_ok=True)

# Load JSON app
load_json_app = get_app("load_json")

for path in lf_json_files:
    file_name = os.path.basename(path).rsplit('.', 1)[0]
    pdf_path = os.path.join(pdf_output_dir, f"{file_name}_GN.pdf")
    lf = load_json_app(path)
    tree = lf.get_ens_tree()
    fig = tree.get_figure(show_support=True, threshold=0.8, height=1200, width=1200).plotly_figure
    # Save the figure as a PDF
    fig.write_image(pdf_path, format='pdf')


Range of JSD


In [47]:
with open ('/Users/gulugulu/repos/PuningAnalysis/results/output_data/species_data.json', 'r') as infile:
    species_data = json.load(infile)

In [48]:
JSD_value_range = []
for name in species_data.keys():
    jsd = species_data[name]['pairwise_jsd']
    JSD_value_range.extend(jsd)

In [49]:
import pandas as pd
jsd_series = pd.Series(JSD_value_range)
description_jsd = jsd_series.describe()
print(description_jsd)

count    277827.000000
mean          0.004648
std           0.006600
min           0.000000
25%           0.000824
50%           0.002249
75%           0.005615
max           0.095827
dtype: float64


In [50]:
# Plot the histogram using Plotly
fig = px.histogram(jsd_series, x=JSD_value_range, nbins=20, title='Histogram of JSD Values', histnorm='percent')
fig.update_layout(
    xaxis_title='JSD Value',
    yaxis_title='Percentage',
    xaxis=dict(
        tickmode='linear',
        tick0=0,
        dtick=0.01  
    )
)
    
fig.show()

Edge branch length range

In [51]:
# Directory and pattern to find JSON files
dir = '../../results/output_data/model_fitting_result_GN'
pattern = os.path.join(dir, '*.json')

# Use glob.glob to find all files matching the pattern
lf_json_files = glob.glob(pattern)

branch_length_range = []
for path in lf_json_files:
    file_name = os.path.basename(path).rsplit('.', 1)[0]
    pdf_path = os.path.join(pdf_output_dir, f"{file_name}_GN.pdf")
    lf = load_json_app(path)
    edge_names = lf.tree.get_node_names(includeself = False, tipsonly=True)
    branch_length_dict = lf.get_lengths_as_ens()
    edge_branch_length_ens = [branch_length_dict[n] for n in edge_names]
    branch_length_range.extend(edge_branch_length_ens)


In [52]:
bl_series = pd.Series(branch_length_range)
description_bl = bl_series.describe()
print(description_bl)

count    5.147000e+03
mean     4.686447e-02
std      5.880938e-02
min      1.298997e-13
25%      6.866823e-03
50%      2.330988e-02
75%      6.937954e-02
max      1.107471e+00
dtype: float64


In [53]:
# Plot the histogram using Plotly
fig_bl = px.histogram(bl_series, x=branch_length_range, nbins=50, title='Histogram of Branch Length', histnorm='percent')
fig_bl.update_layout(
    xaxis_title='Branch Length',
    yaxis_title='Frequency',
        xaxis=dict(
        tickmode='linear',
        tick0=0,
        dtick=0.03  
    )
)
fig_bl.show()